# Scripps Automated Shore Station (SASS) Self-Calibrating SeapHOx (SCS) live data viewer
### This script scrubs .dat files from the SCCOOS dr: https://sccoos.org/dr/data/. The SCS measures pH, oxygen, salinity and temperature. The pH values plotted here are calibrated using an average of the coefficients established pre-deployment and from the  automated tris calibrations. Oxygen concentration has been corrected for salinity and pressure. Before using and sharing these values, please get permission from the author. A new tab delimited text file will be produced every time the script runs, with the current timestamp of the time the file was created. All time zones associated with this script are in UTC.
### Created by: Taylor Wirth twirth@ucsd.edu
### Last edit: 2022 May 3

In [35]:
# load the .py scripts
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os
import glob
%load_ext autoreload
%autoreload 1
%aimport get_recent_dr
%aimport get_all_dr
%aimport correct_DO_with_sal
%aimport pHtris_from_T
%aimport k0int_from_Vint_pHcal
%aimport k0ext_from_Vext_pHcal
%aimport pHint_from_Vint_k0int
%aimport pHext_from_Vext_k0ext
%aimport plot_all

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [36]:
# Get all the files for the Scripps Pier SCS. get_all_dr.py looks and grabs all data files for the Scripps Pier SCS, 
# then converts it into a pandas DataFrame. 
# Printed below is the last hour of data. This may take a few seconds depending on last data download!
#path = 'https://sccoos.org/dr/data/scripps_pier_scs/'
path = 'https://legacy.sccoos.org/dr/data/scripps_pier_scs/'

# if no txt file of downloaded data, get all of the data:
txt = glob.glob('*.txt')
result = [i for i in txt if i.startswith('SIOpierSCS_download')]

if not result: # if there is no downloaded text file, download all data
    df, col_names = get_all_dr.get_all_dr(path)
else: # or download data starting from last downloaded sample
    df, col_names = get_recent_dr.get_recent_dr(path)
    # delete current txt file
    os.remove([i for i in txt if i.startswith('SIOpierSCS')][0])

# create new tab delimited file to download
from datetime import datetime
now = datetime.utcnow()
current_time = now.strftime('%Y%m%d%H%M%S')
df.to_csv('SIOpierSCS_download_'+current_time+'.txt', header=col_names, index=None, sep='\t')

# display important variables
df.iloc[[-6,-5,-4,-3,-2,-1],[7,8,2,3,4,5,6,9,10,11,12,16,17,18,21,22,23,31,33]]

date      time sensor_name  samp_type  samp_num  calib_num  \
14065  2022/05/27  18:40:10      SCS003          0         4          0   
14066  2022/05/27  18:50:10      SCS003          0         5          0   
14067  2022/05/27  19:00:10      SCS003          0         6          0   
14068  2022/05/27  19:10:10      SCS003          0         7          0   
14069  2022/05/27  19:20:10      SCS003          0         8          0   
14070  2022/05/27  19:30:10      SCS003          0         9          0   

       calib_rep  vbatt   vtherm      vint      vext  press     pHint  \
14065          0  16.46 -1.97115  0.072507 -0.912175  2.817  8.162517   
14066          0  16.46 -1.97115  0.072192 -0.912461  2.751  8.156965   
14067          0  16.46 -1.97115  0.072752 -0.911839  2.503  8.166129   
14068          0  16.46 -1.97115  0.072561 -0.911966  2.621  8.162688   
14069          0  16.46 -1.97115  0.072245 -0.912269  2.555  8.157244   
14070          0  16.46 -1.97115  0.072518 -0.911995  2.622  8.161714   

          pHext    O2con    O2sat  O2temp  SBEtemp   SBEsal  
14065  8.213279  343.478  117.897  18.714  18.7450  33.6807  
14066  8.208229  341.094  117.120  18.732  18.7572  33.6871  
14067  8.218047  341.406  117.331  18.775  18.8145  33.6866  
14068  8.215522  342.761  117.830  18.789  18.8299  33.6806  
14069  8.210354  342.169  117.654  18.801  18.8293  33.6848  
14070  8.214726  341.858  117.606  18.825  18.8559  33.6889

In [37]:
# Data QC
# drop data rows if SBE salinity is outside 10 standard deviations
df = df[np.abs(df['SBEsal']-df['SBEsal'].mean()) <= (10*df['SBEsal'].std())]
# remove pressure outliers outside 3 standard deviations
df['press']=df['press'][~(np.abs(df['press']-df['press'].mean()) > (3*df['press'].std()))]

In [38]:
# Oxygen correction for salinity and pressure
df['O2_corr'] = correct_DO_with_sal.correct_DO_with_sal(df.O2con, df.O2temp, df.press, df.SBEsal, sal_input=0)

In [39]:
# run this only once!! separates calibration data from downloaded data file
caldf = df.loc[df['samp_type']==1] # calibration samples
caldf = caldf.rename(columns={"date": "caldate"})
df = df.drop(df[df.samp_type==1].index) # remove calibration samples from the data frame

In [40]:
# calculate in situ tris pH from temperature and calibration coefficients from tris pH
pHtris = pHtris_from_T.pHtris_from_T(caldf.SBEtemp, S=35)
k0int_tris = k0int_from_Vint_pHcal.k0int_from_Vint_pHcal(caldf.vint, pHtris, caldf.SBEtemp)
k0ext_tris = k0ext_from_Vext_pHcal.k0ext_from_Vext_pHcal(caldf.vext, pHtris, caldf.SBEtemp, calsal=35)

tankdf = pd.read_csv([i for i in txt if i.startswith('SCS_tank_calibration')][0],sep='\t') # tank/'factory' calibration coefficients

# add k0's from tris to calibration data frame
caldf.loc[:,'k0int_tris'] = k0int_tris
caldf.loc[:,'k0ext_tris'] = k0ext_tris

# combine calibration data
dfk0 = pd.concat([tankdf, caldf],ignore_index=True,sort=False)
dfk0 = dfk0.drop(columns=['internet_datetime','IP','samp_type','samp_num','calib_num','calib_rep','time',\
    'vbatt','vtherm','vint','vext','isobatt','contemp','pHtemp','press','pHint','pHext',\
    'O2_MN','O2_SN','O2con','O2sat','O2temp','Dphase','Bphase','Rphase','Bamp','Bpot','Ramp','Raw_Temp',\
    'SBEtemp','SBEcond','SBEsal','SBEday','SBEmon','SBEyear','SBEtime','O2_corr'])


In [41]:
# SeapHOx calibration from automated tris measurements
dfk0['caldate'] = pd.to_datetime(dfk0['caldate'])
dfk0 = dfk0.set_index(['sensor_name'])
dfk0 = dfk0.sort_values(by='caldate')
dfk0 = dfk0.reset_index()
print('All calibration coefficients:')
print(dfk0)

All calibration coefficients:
   sensor_name    caldate  k0int_tank  k0int_tris  k0ext_tank  k0ext_tris
0       SCS002 2022-01-18   -0.361933         NaN   -1.358165         NaN
1       SCS002 2022-02-18         NaN   -0.363890         NaN   -1.358733
2       SCS002 2022-02-18         NaN   -0.363718         NaN   -1.358583
3       SCS002 2022-03-04         NaN   -0.363890         NaN   -1.358733
4       SCS002 2022-03-04         NaN   -0.363718         NaN   -1.358583
5       SCS002 2022-03-18         NaN   -0.363169         NaN   -1.358549
6       SCS002 2022-03-18         NaN   -0.363075         NaN   -1.358447
7       SCS002 2022-04-01         NaN   -0.380479         NaN   -1.374578
8       SCS002 2022-04-01         NaN   -0.371263         NaN   -1.365427
9       SCS003 2022-04-04   -0.373082         NaN   -1.404321         NaN
10      SCS003 2022-04-22         NaN   -0.389679         NaN   -1.417942
11      SCS003 2022-04-22         NaN   -0.390035         NaN   -1.418295
12      

In [42]:
# drop calibrations when tris bag was empty
dfk0 = dfk0.drop([7,8])
# drop calibrations when valve was not working
dfk0 = dfk0.drop([10,11,12,13])
dfk0 = dfk0.set_index(['sensor_name'])
print('Calibrations dropped due to empty tris bag: rows 7 and 8')
print(dfk0)

Calibrations dropped due to empty tris bag: rows 7 and 8
               caldate  k0int_tank  k0int_tris  k0ext_tank  k0ext_tris
sensor_name                                                           
SCS002      2022-01-18   -0.361933         NaN   -1.358165         NaN
SCS002      2022-02-18         NaN   -0.363890         NaN   -1.358733
SCS002      2022-02-18         NaN   -0.363718         NaN   -1.358583
SCS002      2022-03-04         NaN   -0.363890         NaN   -1.358733
SCS002      2022-03-04         NaN   -0.363718         NaN   -1.358583
SCS002      2022-03-18         NaN   -0.363169         NaN   -1.358549
SCS002      2022-03-18         NaN   -0.363075         NaN   -1.358447
SCS003      2022-04-04   -0.373082         NaN   -1.404321         NaN
SCS003      2022-05-27         NaN   -0.380811         NaN   -1.400558
SCS003      2022-05-27         NaN   -0.380798         NaN   -1.400521


In [43]:
# calculate calibration coefficients for each sensor
k0int_mean = []
k0ext_mean = []
unq_sen = dfk0.index.unique()

# loop through sensor names/deployments
for i in range(0,len(unq_sen)):
    k0int = dfk0.loc[unq_sen[i]].k0int_tank.tolist()
    k0ext = dfk0.loc[unq_sen[i]].k0ext_tank.tolist()
    if isinstance(dfk0.loc[unq_sen[i]].k0int_tank.tolist(),float):
        k0int_mean.append(np.nanmean(k0int))
        k0ext_mean.append(np.nanmean(k0ext))
        print(unq_sen[i] + ' k0int_tank_only = ', k0int_mean[i])
        print(unq_sen[i] + ' kext_tank_only = ', k0ext_mean[i])
        continue
    
    # append the k0's to calculate the means of all k0's
    k0int.extend(dfk0.loc[unq_sen[i]].k0int_tris.tolist())
    k0ext.extend(dfk0.loc[unq_sen[i]].k0ext_tris.tolist())
    k0int_mean.append(np.nanmean(k0int))
    k0ext_mean.append(np.nanmean(k0ext))
    print(unq_sen[i] + ' k0int_mean = ', k0int_mean[i])
    print(unq_sen[i] + ' kext_mean = ', k0ext_mean[i])

SCS002 k0int_mean =  -0.363341874042181
SCS002 kext_mean =  -1.3585419207112064
SCS003 k0int_mean =  -0.3782303333333334
SCS003 kext_mean =  -1.4017999999999997


In [44]:
# plot calibration coefficients
figs = {} # container for figures
for p in range(0,len(unq_sen)):
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(x=dfk0.loc[[unq_sen[p]]].caldate, y=dfk0.loc[[unq_sen[p]]].k0int_tank,mode='markers',name='k0int_tank',\
        marker_symbol='star',marker_size=15,marker_color='green'),secondary_y=False)
    fig.add_trace(go.Scatter(x=dfk0.loc[[unq_sen[p]]].caldate, y=dfk0.loc[[unq_sen[p]]].k0ext_tank,mode='markers',name='k0ext_tank',\
        marker_symbol='square',marker_size=10,marker_color='black'),secondary_y=True)
    fig.add_trace(go.Scatter(x=dfk0.loc[[unq_sen[p]]].caldate, y=dfk0.loc[[unq_sen[p]]].k0int_tris,mode='markers',name='k0int_tris',\
        marker_symbol='star',marker_size=15,marker_color='blue'),secondary_y=False)
    fig.add_trace(go.Scatter(x=dfk0.loc[[unq_sen[p]]].caldate, y=dfk0.loc[[unq_sen[p]]].k0ext_tris,mode='markers',name='k0ext_tris',\
        marker_symbol='square',marker_size=10,marker_color='red'),secondary_y=True)
    fig.add_hline(y=float(k0int_mean[p]),secondary_y=False,name='k0int_mean',line_color='blue',annotation_text="k0 means",annotation_position="top left") # mean k0int for all calibrations
    fig.add_hline(y=float(k0ext_mean[p]),secondary_y=True,name='k0int_mean',line_color='red') # mean k0ext for all calibrations
    fig.update_layout(height=500, width=950,title_text=unq_sen[p] + ' Calibration coefficients at 0C')
    fig['layout']['yaxis']['title']='k0_int'
    fig['layout']['yaxis2']['title']='k0_ext'
    figs['fig'+str(p)] = fig

for p in range(0,len(unq_sen)):     
    figs[list(figs)[p]].show()

In [45]:
# add tris pH and sensor pH during automated tris calibrations
caldf.loc[:,'pHtris'] = pHtris
caldf.loc[:,'pHint_tris'] = pHint_from_Vint_k0int.pHint_from_Vint_k0int(k0int_mean[0], caldf.vint, caldf.SBEtemp)
caldf.loc[:,'pHext_tris'] = pHext_from_Vext_k0ext.pHext_from_Vext_k0ext(k0ext_mean[0], caldf.vext, caldf.SBEtemp, 35)


In [46]:
# calcuate calibrated pHint and pHext
df['datetime'] = list(df['date'] + ' ' + df['time']) # combine date and time to use for plots
pHint_cal = []
pHext_cal = []

for p in enumerate(unq_sen):
    pHint_SBE = pHint_from_Vint_k0int.pHint_from_Vint_k0int(k0int_mean[p[0]], df.loc[df.sensor_name==p[1]].vint, df.loc[df.sensor_name==p[1]].SBEtemp)
    #pHdf[p[1]+'_pHint'] = pHint_SBE
    pHint_cal = pHint_cal + (list(pHint_SBE))
    pHext_SBE = pHext_from_Vext_k0ext.pHext_from_Vext_k0ext(k0ext_mean[p[0]], df.loc[df.sensor_name==p[1]].vext, df.loc[df.sensor_name==p[1]].SBEtemp, df.loc[df.sensor_name==p[1]].SBEsal)
    #pHdf[p[1]+'_pHext'] = pHext_SBE
    pHext_cal = pHext_cal + (list(pHext_SBE))

# add calibrated pH to the data frame

df['pHint_cal'] = pHint_cal
df['pHext_cal'] = pHext_cal

In [47]:
# load local precipation data from text file
pdf = pd.read_csv('SD_precip.txt',sep='\t')
pdf = pdf.replace('T', np.nan)
pdf['date'] = pd.to_datetime(pdf.date)
pdf = pdf.astype({'maxtemp': int, 'mintemp': int, 'avetemp': int, 'deptemp': int, 
    'HDD': int, 'CDD': int, 'prec': float})

df.datetime = pd.to_datetime(df.datetime) # set main dataset timestamp back into pandas datatime

In [48]:
# save calibrated data to text file
# now = datetime.utcnow()
# current_time = now.strftime('%Y%m%d%H%M%S')
# df.to_csv('SIOpierSCS_calibrated_'+current_time+'.txt', index=None, sep='\t')

In [49]:
# load discrete bottle sample data from file
txt = glob.glob('*.txt')
ddf = pd.read_csv([i for i in txt if i.startswith('SIOpier_discrete.txt')][0],sep='\t')

# Run this if new discrete samples are to be used
# import PyCO2SYS as pyco2
# ddf = pd.read_excel('SIOpier_discrete.xlsx')
# sal_diff = np.mean(ddf.Salinity_CTD - ddf.Salinity_martz)

# # CO2SYS input paramaters from discrete bottle data
# kwargs = dict(
#     par1_type = 3,  # The first parameter supplied is of type "2", which means "pH"
#     par1 = ddf.pH_spec,  # value of the first parameter
#     par2_type = 1,  # The second parameter supplied is of type "3", which means "alkalinity" estimated as 2250 umol/kg
#     par2 = 2250,  # value of the second parameter
#     salinity = ddf.Salinity_martz+sal_diff,  # Salinity of the sample
#     temperature = ddf.temp_spec,  # Temperature at input conditions
#     temperature_out = ddf.temp_insitu,  # Temperature at output conditions
#     pressure = 0,  # Pressure at input conditions - atmosphere
#     pressure_out = 3,  # Pressure at output conditions - 3 dbar
#     total_silicate = 0,  # Concentration of silicate  in the sample (in umol/kg)
#     total_phosphate = 0,  # Concentration of phosphate in the sample (in umol/kg)
#     opt_pH_scale = 1,  # pH scale at which the input pH is reported ("1" means "Total Scale")
#     opt_k_carbonic = 4,  # Choice of H2CO3 and HCO3- dissociation constants K1 and K2 ("4" means "Mehrbach refit")
#     opt_k_bisulfate = 1,  # Choice of HSO4- dissociation constant KSO4 ("1" means "Dickson")
#     opt_total_borate = 1,  # Choice of boron:sal ("1" means "Uppstrom")
# )
    
# results = pyco2.sys(**kwargs)
# ddf['pH_insitu'] = results['pH_total_out'] 
# ddf.to_csv('SIOpier_discrete.txt', index=None, sep='\t')

In [50]:
# fun part! plot it all
plot_all.plot_all(unq_sen,df,df.datetime,df.pHint_cal,df.pHext_cal,df.O2_corr,df.O2sat,df.SBEtemp,df.O2temp,df.pHtemp,df.SBEsal,df.press,pdf,ddf)